# Data Visualisation - Lab 2 - Data Passing

---

**Authors: Claire Rocks and Richard Kirk**

---

Welcome to the second lab for Data Visualisation.

In this lab we are going to look at bit more at acquiring data and pre-processing it before visualisation.

The first step is to load some data into your application.  Unless you own the data and its stored in a certain way, things can get a little messy.  

  * How do you find good sources?
  * Do you have the right to use the data?
  * Is the data extracted in a format that is easy for the application to use?
  * What to do when the data set is very large?

In this lab, we will introduce some possible data sources.  We'll also have a look at a few different techniques we can use to both get data, and how to treat the data to make sure that it is clean and ready to be utilised.


## Acquiring Data

Using good search terms in your search engine is a good start when looking for data sets, specifying the file format or whether it is a feed/downloadable file might yield better search results than more general search terms.

There are also many sites that are very good for acquiring datasets, e.g.

  * [Kaggle](https://www.kaggle.com/)
  * [UK government](https://data.gov.uk/)
  * [Google Cloud](https://cloud.google.com/datasets)
  * [NASA](https://www.earthdata.nasa.gov/)

Other organisations make their data available through APIs, e.g.

  * [OECD API](https://data.oecd.org/api/)
  * [Kaggle API](https://www.kaggle.com/docs/api)
  * [Twitter API](https://developer.twitter.com/en/docs/twitter-api)

Where there existing data sets and no APIs to help you generate one, you might find yourself scraping data from the web.


## Parsing data

Data comes in all shapes and sizes, whether that be from large data sets that are used to [picture black holes](https://www.extremetech.com/extreme/289423-it-took-half-a-ton-of-hard-drives-to-store-eht-black-hole-image-data) to small datasets like the [iris dataset](https://en.wikipedia.org/wiki/Iris_flower_data_set). However, in nearly all cases, the data needs to be preprocessed in order to avoid anomalies from ruining our visualisations. 

Parsing data coverts a raw stream of data into a structure that can be manipulated in our application - for the most part we are looking to get data into a pandas DataFrame

## Setup for the Lab
First up, lets set up some key libraries that we will require for the rest of the lab. This includes:
  * ```pandas``` - used to store the data
  * ```matplotlib``` - used to plot some graphs
  * ```numpy``` - used to import common maths functions
  * ```seaborn``` - used to import a collection of data

In [ ]:
%pip install numpy pandas seaborn matplotlib
import matplotlib.pyplot as plt
import seaborn as sns
import pandas as pd
import numpy as np

## Data cleanup
In many cases, data coming from raw sources can require cleaning up. Examples of this occurring includes:
  * Sensors fail or need recalibrating
  * Users enter one too many/few 0's when entering how many of an item they want
  * Reviews writing things in subtly different ways but meaning the same thing
  * Data availability etc.

As such, we need to make some decision about what to do with that data when we are analysing and visualising the data. There are multiple stages to cleaning the data, some of which will be described here.

### Invalid data
When collecting data that will later be analysed, there will be occasions where the data is not available or is not a valid value. As such, we need to be able to detect these, and correct as appropriate.

Lets take a hypothetical movie database. In this database, the cast and crew of a large body of films have been stored. These films span the full range, from massive blockbusters to small indie projects. For many larger films, the cast and crew will be properly documented due to the film's popularity. However, the smaller the film, the less likely the cast and crew will be provided. This could be for multiple reasons, maybe it is an old film and nobody knows now, maybe there was a dispute about the film, maybe a person is embarrassed by the film and wants to remove their association.

Invalid data may not just be the absence of data. Say, for example, the finances and box office earnings were also stored on this database. Again, for larger films, these are made public, validated and (often) boasted about by production companies. On the other hand, small films are not tracked anywhere near as thoroughly, so may not report these values so could get scored as 0.

We therefore need to take action to show that, in the above example, there are a considerable amount of films both made by and starring nobody that also cost an amount of money to produce.

Checking for invalid data is very much dependant on the type of data you are examining. Therefore, we need different techniques for different situations. In some cases, the data can be stored as N/A. Where there are many N/As we need to make a decision about what we are going to do with them.  

We might want to delete them and Python has a handy function for this! In the example shown in the function definition, we have a synthetic data frame which contains a N/A field (represented by ```np.nan``` and ```pd.NaT```. These can be used interchangeability in this case). By using the function ```dropna``` on a given dataframe, we can get rid of all the rows with these in them.

In [ ]:
?pd.DataFrame.dropna

We might also want to replace missing data with another value such as replacing the value with the mean of the dataset, or the mean of the previous 3 or values, or the median of the data.  

Python also has a handy function for this, `replace`!

  * `df['column name'] = df['column name'].replace(['old value'],'new value')`

This function replaces an old value with a new value in a single column. We can also do this with multiple values or across the entire dataset:

  * `df['column name'] = df['column name'].replace(['1st old value','2nd old value',...],'new value')`

  * `df = df.replace(['old value'],'new value')`

What you do will be dependant on the data, and the insights you are trying to gain or show.


### Passing numerical data
There are always outliers and exceptions to every case, and again we need to decide if they are genuine or mistakes, and whether including them helps us. For example, consider the following data set:

In [ ]:
taxis = sns.load_dataset('taxis')
taxis

If you have a look at entry 6429, you can see that the distance is a lot larger than the others surrounding it. We can see how far it is outside the mean through Python, as well as calculating the number of standard deviations away the entry is.

In [ ]:
## Finding the mean
print("Mean:", np.mean(taxis['distance']))
print("Entry 6429 distance from mean: ",
      np.abs(taxis['distance'][6429] - np.mean(taxis['distance'])))

print()

## Finding the standard deviation
print("Standard Deviation:", np.std(taxis['distance'], ddof=1))
print("Number of standard deviations entry 6429 is from mean: ",
      np.abs(taxis['distance'][6429] - np.mean(taxis['distance']))/np.std(taxis['distance'], ddof=1))

In this case, we could for example choose to leave the value alone, replace the value with the mean or delete the row entirely before performing the visualisation. Lets try replacing it with the mean...

In [ ]:
taxis['distance'][6429]=np.mean(taxis['distance'])
taxis.tail()

Or deleting the row entirely

In [ ]:
taxis = taxis.drop(index=[6429])
taxis.tail()

You can also remove multiple rows by specifying the index range.

In [ ]:
taxis1 = taxis.drop(taxis.index[6427:6431])
taxis1.tail()

You may also have to convert the data types. This may involve writing custom functions for example to replace *$* or *£* signs before using a function like `pd.to_numeric()` - we'll see an example of this a bit later in the lab.

### Rearranging Data Frames

In some cases, we may need to rearrange the data frames themselves. This allows for better readability, as well as selecting only particular columns and rows. This is referred to as *melting* the data. This can get complex quite quick, so the Pandas library in Python has a handy `melt` function. 

The `melt()` function is used to unpivot a given DataFrame from wide format to long format. It is also useful to reformat a DataFrame into a format where one or more columns are identifier variables, while all other columns, considered measured variables, are unpivoted to the row axis.

In [ ]:
# creating a dataframe
df = pd.DataFrame({'Name': {0: 'Claire', 1: 'Richard', 2: 'Bob'},
                   'Favourite Food': {0: 'Sushi', 1: 'Pizza', 2: 'Sandwiches'},
                   'Age': {0: 27, 1: 23, 2: 21}})
df

In [ ]:
# Name is id_vars and Favourite Food is value_vars
pd.melt(df, id_vars =['Name'], value_vars =['Favourite Food'])

In [ ]:
# multiple unpivot columns
pd.melt(df, id_vars =['Name'], value_vars =['Favourite Food', 'Age'])

More information on this function can be found by running the code block below.

In [ ]:
?pd.melt

## Data scrapping

**PLEASE NOTE: Because this is all based off of live websites, the website may change its underlying structure, so may break the code presented in this section at any moment. However, the principles covered should still apply**

The web is full of data, most of which cannot be gained through API's or pre-prepared datasets. In these cases, we need to gather this data ourselves through the use of data scrapping. In this section, we will be going through an example to collect some data from a public website.

For this section, we will be using the following libraries:
  * ```beautifulsoup4``` - HTML and XML parser (more info can be found [here](https://www.crummy.com/software/BeautifulSoup/bs4/doc/))
  * ```pandas``` - stores data in a nice format for data analysis
  * ```requests``` - allows for requests to be made to external websites for files

In [ ]:
%pip install beautifulsoup4 pandas requests
from bs4 import BeautifulSoup
import pandas as pd
import requests

### Downloading a webpage

Steam is one of the most popular PC gaming platform in the world. Wouldn't it be cool to get the prices of different games across different countries and search terms? To start this off, we need to construct the URL. Fortunately, Steam allows you to specify the country code and the term you want to search in the URL. We can then use **BeautifulSoup** to pass the the data using the `html.parser` ... parser. We can use `prettify` to see all the content on the page.

In [ ]:
## Getting the webpage with a given search term
searchTerm = '' ## Add string here to determine what you want to search. If blank, searches for all
countryCode = 'uk' ## Change this if you want to explore game prices in different countries
url = 'https://store.steampowered.com/search/?cc=' + countryCode + '&term=' + searchTerm
page = requests.get(url)

## Parse the contents using the html parser
soup = BeautifulSoup(page.content, "html.parser")

## Uncomment this to show the page
#soup.prettify()

### Finding the data items

When we have a look at the page (either using the `prettify` or by using the inspector on any browser), we can see that each game is contained within an `a` tag with the class `search_result_row ds_collapse_flag`. As such, we can use BeautifulSoup to find all of these, using the aptly-named `find_all` function!

**NB: If you are running this using a non-UK version of Steam, you will need to add a space at the end of the class name...**

When we have a look at a single result, you'll see it is still in raw HTML, and doesn't look great...

In [ ]:
## Find all "a" tags, with a given class value
results = soup.find_all("a", class_="search_result_row ds_collapse_flag")  ##If running on the UK version of Steam
#results = soup.find_all("a", class_="search_result_row ds_collapse_flag ")  ##If running on other versions of Steam

## Lets print out the first value, just to check it
results[0]

### Finding the data within each element

Now that we have all the game items, we can have a look inside and extract the key information that we need. For now, lets just print out the raw data, so we can see how we need to clean it.

In [ ]:
## For each item in the results list...
for item in results:
    game_name = item.find("span", class_="title") ## ... find the title
    game_price = item.find("div", class_="col search_price responsive_secondrow") ## ... find the price (only set if no discount)
    game_discount = item.find("div", class_="col search_discount responsive_secondrow") ## ... find the discounts
    if (game_price == None):
        game_price = item.find("div", class_="col search_price discounted responsive_secondrow") ## ... find the price if there is a discount

    ## Print out the details
    print(game_name.text.strip())
    print(game_discount.text.strip())
    print(game_price.text.strip())
    print('========================')

### Storing the data into a data frame

Now that we know how the data is structured, we can sanitise the data and store it all in a **pandas** data frame. This code looks complex, but it can be broken down into multiple small sections. With something like this, it often helps to split the work up into small sections. In this case, we first get the name of the game, then the discount, then the game price (getting this depends on whether there is a discount on the game, and whether the game is free or not).

**NB: If you are running on the non-UK version of Steam, you will need to change all "£" to an appropriate currency character or set of characters**

In [ ]:
## Lets create some arrays to store the data for each column
game_names = []
game_discounts = []
game_prices_org = []
game_prices_discount = []

## For each result...
for item in results:
    ## ... get and store the name
    game_name = item.find("span", class_="title").text.strip()
    game_names.append(game_name)

    ## ... get and store the discount, sanitising if no discount is present
    game_discount = item.find("div", class_="col search_discount responsive_secondrow").text.strip()
    if game_discount == "" or game_discount == None:
        game_discount = "0%"
    game_discounts.append(game_discount)

    ## ... get and store the price(s)
    game_price = item.find("div", class_="col search_price responsive_secondrow")

#If there is no game price available, then there may be a discount instead
    if game_price == None:
        if '0%' != game_discount:
            ## If there is a discount, then split the string on the '$' symbol, and add to relevant arrays
            game_price = item.find("div", class_="col search_price discounted responsive_secondrow").text.strip()
            if 'Free' in game_price: #Sometimes a game that costs £0 goes on sale, so we should check for that
                game_price = game_price.replace('Free', '£0.00')
            game_prices_org.append("£"+game_price.split('£')[1])
            game_prices_discount.append("£"+game_price.split('£')[2])
        else: #Or it is something weird, so lets put in a blank piece of data
            game_price = ''
            game_prices_org.append(game_price)
            game_prices_discount.append(game_price)
    else:
        game_price = game_price.text.strip()
        if 'Free' in game_price: #If it is a free-to-play game, we want to sanatise the data such that it shows up as $0
            game_price = '£0.00'
            game_prices_org.append(game_price)
            game_prices_discount.append(game_price)
        else:
            ## If no discount, sanitise and add the price to both the "discount" and regular price
            game_prices_org.append(game_price)
            game_prices_discount.append(game_price)

## Generate and preview the data frame
dataFrame = pd.DataFrame({"Name":game_names, "Discount":game_discounts, "Original Price":game_prices_org, "Discounted Price":game_prices_discount})

dataFrame

The values for the Original Price and Discounted Price are a bit messy - they are including data about the currency, they sometimes have commas and sometimes have spaces - we can write a custom function to clean this up

In [ ]:
def convert_currency(val):
    new_val = val.replace(',','').replace('£', '').replace('$', '').replace('NT', '').replace(' ', '')
    #print(new_val)
    return pd.to_numeric(new_val)

dataFrame['Sanitised Original Price'] = dataFrame['Original Price'].apply(convert_currency)
dataFrame.dtypes

## Exercises
### Exercise 1 - Analysing scrapped data
Using the Steam game data provided above, find the following information:
  * The average original price
  * The average discounted price
  * The average discount where one is applied
  * The average discounted price where a discount has been applied
  * Any anomalous results (there may be none present)

In [ ]:
## Exercise 1 code here! ##

### Exercise 2 - Adding more data
When scrapping the data from Steam, more information than just the name, discount and price (both with and without the discount) were given. As such, modify the scraping tools to produce a new, more complete data frame for all the Steam data:
  * Date of release
  * Percentage of positive reviews
  * Number of reviews

In [ ]:
## Exercise 2 code here! ##

## Bonus Exercises
The BBC weather website has a connected RSS feed, that allows users to pull information about the current weather for a given region (depending on a 7 digit ID number). For example, if you go [here](https://weather-broker-cdn.api.bbci.co.uk/en/observation/rss/2652221), you get the weather data for Coventry in a handy XML format. By changing the last 7 digits to a different ID number, you can get the weather somewhere else in the country.

### Bonus exercise 1 - Exploring data
Examine the weather for the following places:
 * Kenilworth (ID: 2645822)
 * Washington DC (ID: 4140963)
 * Sydney (ID: 2147714)

-----

**Bonus Exercise notes here!**

-----

### Bonus exercise 2 - Scrapping weather data
Using the knowledge from data scrapers and data passing, produce a Data Frame storing the information for 1000 ID values (for example, all ID's between 2645000 and 2646000 or 1000 random unique ID's):

  * ID
  * Place Name
  * Place Latitude
  * Place Longitude
  * Time
  * Temperature
  * Wind direction
  * Wind speed
  * Humidity
  * Pressure
  * Visibility

  **NB:** Some IDs may not be valid, so you may not get 1000 valid entries. An example of non-valid ID's include [2652230](https://weather-broker-cdn.api.bbci.co.uk/en/observation/rss/2652230). In these cases, no data should be stored for these IDs.

In [ ]:
## Bonus Exercise 2 code here! ##